# **HeartView Pipeline for Actiwave Cardio and Other ECG Sources**
## ECG Signal Quality Assessment

This notebook presents an example of the HeartView pipeline's functionalities on some sample ECG data.

### 1. Import Modules

In [1]:
from sys import path
path.append('../')
from heartview import heartview
from heartview.pipeline import ECG, SQA
import pandas as pd
import matplotlib.pyplot as plt

### 2. Load Data

#### 2-a. Load Data of Actiwave Cardio

In [2]:
edf = 'sample_actiwave.edf'
ecg, acc = ECG.read_actiwave(edf)
data = ecg
display(ecg.head(), acc.head())

Timestamp        mV
0 2016-07-20 14:31:00.000000  0.992463
1 2016-07-20 14:31:00.000977  0.995095
2 2016-07-20 14:31:00.001953  0.989246
3 2016-07-20 14:31:00.002930  0.954444
4 2016-07-20 14:31:00.003906  0.921396

Timestamp         X         Y         Z  Magnitude
0 2016-07-20 14:31:00.000000  6.738466  7.041151  1.871547   9.924083
1 2016-07-20 14:31:00.031250  6.738466  6.834366  1.871547   9.778455
2 2016-07-20 14:31:00.062500  6.840360  7.041151  2.162243  10.052046
3 2016-07-20 14:31:00.093750  6.840360  7.041151  2.066343  10.031854
4 2016-07-20 14:31:00.125000  6.738466  6.834366  1.871547   9.778455

#### 2-b. Load Data of Other EEG Sources

In [15]:
file = 'sample_ecg.csv'
data = pd.read_csv(file)
data.head()

Timestamp        mV
0  2016-10-14 10:10:51.000000 -0.206620
1  2016-10-14 10:10:51.000977 -0.197554
2  2016-10-14 10:10:51.001953 -0.186148
3  2016-10-14 10:10:51.002930 -0.197847
4  2016-10-14 10:10:51.003906 -0.190243

### 3. Setup Data

Set the parameters of your data, such as the sampling rate `fs` (Hz) and segment size `seg_size` (seconds).

In [4]:
fs = 1024
seg_size = 60

Segment your data into 60-second windows.

In [5]:
data = heartview.segment_data(data, fs, seg_size)
data

Segment                  Timestamp        mV
0             1 2016-07-20 14:31:00.000000  0.992463
1             1 2016-07-20 14:31:00.000977  0.995095
2             1 2016-07-20 14:31:00.001953  0.989246
3             1 2016-07-20 14:31:00.002930  0.954444
4             1 2016-07-20 14:31:00.003906  0.921396
...         ...                        ...       ...
185339        4 2016-07-20 14:34:00.995117  0.000152
185340        4 2016-07-20 14:34:00.996094  0.000152
185341        4 2016-07-20 14:34:00.997070  0.000152
185342        4 2016-07-20 14:34:00.998047  0.000152
185343        4 2016-07-20 14:34:00.999023  0.000152

[185344 rows x 3 columns]

### 4. Filter Data

Filter out any 60-Hz powerline interference, baseline wander, and muscle noise.

In [6]:
data['Powerline'] = ECG.powerline_int_filter(data['mV'], fs, q = 20, freq = 60)
data['Filtered'] = ECG.baseline_muscle_filter(data['Powerline'], 0.5, 45, fs, order = 4)
data.head()

Segment                  Timestamp        mV  Powerline  Filtered
0        1 2016-07-20 14:31:00.000000  0.992463   0.984312  0.076108
1        1 2016-07-20 14:31:00.000977  0.995095   0.986809  0.057566
2        1 2016-07-20 14:31:00.001953  0.989246   0.981974  0.039494
3        1 2016-07-20 14:31:00.002930  0.954444   0.949227  0.022434
4        1 2016-07-20 14:31:00.003906  0.921396   0.919016  0.006851

### 5. Assess Signal Quality

##### First, detect the number of peaks (i.e., heartbeats) in each segment of the signal. Save each peak occurrence in a `Peak` column in the data frame.

In [7]:
peak_ix = ECG.detect_rpeaks(data, 'Filtered', fs)
data.loc[peak_ix, 'Peak'] = 1
data.head()

Segment                  Timestamp        mV  Powerline  Filtered  Peak
0        1 2016-07-20 14:31:00.000000  0.992463   0.984312  0.076108   NaN
1        1 2016-07-20 14:31:00.000977  0.995095   0.986809  0.057566   NaN
2        1 2016-07-20 14:31:00.001953  0.989246   0.981974  0.039494   NaN
3        1 2016-07-20 14:31:00.002930  0.954444   0.949227  0.022434   NaN
4        1 2016-07-20 14:31:00.003906  0.921396   0.919016  0.006851   NaN

We can quickly verify that peaks have been detected.

In [8]:
data['Peak'].sum()

318.0

##### Compute second-by-second mean heart rate (HR) and interbeat interval (IBI) values and label all invalid values.

In [9]:
interval_data = ECG.get_seconds(data, 'Peak', fs, seg_size)
interval_data

Segment  Second           Timestamp     Mean HR    Mean IBI  # R Peaks  \
0          1       1 2016-07-20 14:31:00  111.203620  539.550781        1.0   
1          1       2 2016-07-20 14:31:01  111.573850  537.760417        2.0   
2          1       3 2016-07-20 14:31:02  111.573850  537.760417        2.0   
3          1       4 2016-07-20 14:31:03  113.288261  529.622396        2.0   
4          1       5 2016-07-20 14:31:04  114.200743  525.390625        2.0   
..       ...     ...                 ...         ...         ...        ...   
176        3     177 2016-07-20 14:33:56  108.455428  553.222656        1.0   
177        3     178 2016-07-20 14:33:57  106.297578  564.453125        2.0   
178        3     179 2016-07-20 14:33:58  105.265563  569.986979        2.0   
179        4     180 2016-07-20 14:33:59  105.931034  566.406250        2.0   
180        4     181 2016-07-20 14:34:00         NaN         NaN        0.0   

     Invalid  
0          0  
1          0  
2          0  
3          0  
4          0  
..       ...  
176        0  
177        0  
178        0  
179        0  
180        0  

[181 rows x 7 columns]

##### Compute the SQA metrics by segment.

In [10]:
peaks_by_seg = SQA.evaluate_peaks(interval_data, seg_size)
peaks_by_seg.head()

Segment           Timestamp  Detected    Expected
0       1 2016-07-20 14:31:00     110.0  111.153347
1       2 2016-07-20 14:32:00     102.0   98.937198
2       3 2016-07-20 14:33:00     106.0  104.077622
3       4 2016-07-20 14:34:00       0.0         NaN

In [11]:
sqa = SQA.compute_metrics(peaks_by_seg)
sqa

Segment           Timestamp  Detected    Expected  Invalid   Missing  \
0       1 2016-07-20 14:31:00     110.0  111.153347        0  1.153347   
1       2 2016-07-20 14:32:00     102.0   98.937198        0  0.000000   
2       3 2016-07-20 14:33:00     106.0  104.077622        0  0.000000   
3       4 2016-07-20 14:34:00       0.0         NaN        1  0.000000   

   % Missing  
0   1.037618  
1   0.000000  
2   0.000000  
3   0.000000

## Visualize Data

##### Visualize the raw and filtered ECG signal during Segment 1.

In [12]:
heartview.plot_signal(data, 'Timestamp', ['mV', 'Filtered'], fs, seg_size, segment = 1, signal_type = 'ecg')

##### Visualize the expected-to-missing numbers of beats per segment.

In [13]:
SQA.plot_expected2missing(sqa, title = 'Sample ECG')